In [99]:
!pip install mysql-connector-python


✅ Connected successfully!


In [108]:
import pandas as pd

# Load the dataset
df = pd.read_csv("C:/Users/user/Desktop/CapstoneProject/traffic_stops - traffic_stops_with_vehicle_number (1).csv")

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 65538 entries, 0 to 65537
Data columns (total 16 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   stop_date           65538 non-null  object
 1   stop_time           65538 non-null  object
 2   country_name        65538 non-null  object
 3   driver_gender       65538 non-null  object
 4   driver_age_raw      65538 non-null  int64 
 5   driver_age          65538 non-null  int64 
 6   driver_race         65538 non-null  object
 7   violation_raw       65538 non-null  object
 8   violation           65538 non-null  object
 9   search_conducted    65538 non-null  bool  
 10  search_type         43818 non-null  object
 11  stop_outcome        65538 non-null  object
 12  is_arrested         65538 non-null  bool  
 13  stop_duration       65538 non-null  object
 14  drugs_related_stop  65538 non-null  bool  
 15  vehicle_number      65538 non-null  object
dtypes: bool(3), int64(2), 

C:\Users\user\AppData\Local\Temp\ipykernel_6048\254287914.py:4: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("C:/Users/user/Desktop/CapstoneProject/traffic_stops - traffic_stops_with_vehicle_number (1).csv")


In [109]:
# remove columns that contain missing values
df.dropna(axis=1, how='all', inplace=True)

# combine stop_date and stop_time into a single column
if 'stop_date' in df.columns and 'stop_time' in df.columns:
 
    df['stop_datetime'] = pd.to_datetime(df['stop_date'] + ' ' + df['stop_time'])
    df.drop(columns=['stop_date', 'stop_time'], inplace=True)

df=df.where(pd.notnull(df),None)
print(df.head())

  country_name driver_gender  driver_age_raw  driver_age driver_race  \
0       Canada             M              59          19       Asian   
1        India             M              35          58       Other   
2          USA             M              26          76       Black   
3       Canada             M              26          76       Black   
4       Canada             M              62          75       Other   

      violation_raw violation  search_conducted     search_type stop_outcome  \
0     Drunk Driving  Speeding              True  Vehicle Search       Ticket   
1             Other     Other             False  Vehicle Search       Arrest   
2  Signal Violation  Speeding             False           Frisk       Ticket   
3          Speeding       DUI              True           Frisk      Warning   
4          Speeding     Other             False  Vehicle Search       Arrest   

   is_arrested stop_duration  drugs_related_stop vehicle_number  \
0         True     

In [110]:
import mysql

In [117]:
import mysql.connector as conn
from datetime import datetime

mydb = mysql.connector.connect(
    host="localhost",
    user="root",
    password="Sql@pass3",
    database="Police_SC"
)

print("✅ Connected successfully!")

✅ Connected successfully!


In [118]:
cur = mydb.cursor() 

In [119]:
cur.execute('USE Police_SC;')

In [120]:
cur.execute('''
CREATE TABLE traffic_stops (
    stop_id INT AUTO_INCREMENT PRIMARY KEY,
    country_name VARCHAR(100),
    driver_gender VARCHAR(20),
    driver_age_raw VARCHAR(10),
    driver_age INT,
    driver_race VARCHAR(50),
    violation_raw VARCHAR(255),
    violation VARCHAR(255),
    search_conducted BOOLEAN,
    search_type VARCHAR(255),
    stop_outcome VARCHAR(100),
    is_arrested BOOLEAN,
    stop_duration VARCHAR(50),
    drugs_related_stop BOOLEAN,
    vehicle_number VARCHAR(50),
    stop_datetime DATETIME
    )
''');
print("Table Created")

Table Created


In [87]:
print(df)

      country_name driver_gender  driver_age_raw  driver_age driver_race  \
0           Canada             M              59          19       Asian   
1            India             M              35          58       Other   
2              USA             M              26          76       Black   
3           Canada             M              26          76       Black   
4           Canada             M              62          75       Other   
...            ...           ...             ...         ...         ...   
65533        India             F              54          48       Black   
65534       Canada             F              18          35    Hispanic   
65535          USA             M              27          41       Asian   
65536       Canada             F              49          63       Black   
65537          USA             F              72          32       Other   

          violation_raw violation  search_conducted     search_type  \
0         Drunk 

In [ ]:
for _, row in df.iterrows():
    query = """
    INSERT INTO traffic_stops (
       country_name, driver_gender, driver_age_raw, driver_age,
        driver_race, violation_raw, violation, search_conducted, search_type,
        stop_outcome, is_arrested, stop_duration, drugs_related_stop, vehicle_number,stop_datetime
    ) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
    """
    
    values = (
         row['country_name'], row['driver_gender'], row['driver_age_raw'], row['driver_age'],
        row['driver_race'], row['violation_raw'], row['violation'], row['search_conducted'], row['search_type'],
        row['stop_outcome'], row['is_arrested'], row['stop_duration'], row['drugs_related_stop'], row['vehicle_number'],row['stop_datetime']
    )
    
    cur.execute(query, values)
mydb.commit()




country_name                       Canada
driver_gender                           M
driver_age_raw                         59
driver_age                             19
driver_race                         Asian
violation_raw               Drunk Driving
violation                        Speeding
search_conducted                     True
search_type                Vehicle Search
stop_outcome                       Ticket
is_arrested                          True
stop_duration                   16-30 Min
drugs_related_stop                   True
vehicle_number                 UP76DY3473
stop_datetime         2020-01-01 00:00:00
Name: 0, dtype: object
country_name                        India
driver_gender                           M
driver_age_raw                         35
driver_age                             58
driver_race                         Other
violation_raw                       Other
violation                           Other
search_conducted                    False
search_type

In [ ]:

cur.close()
conn.close()